In [19]:
import numpy as np
import pandas as pd
from scipy.stats import norm
np.set_printoptions(suppress=True)
import csv
from numpy import nan
import matplotlib.pyplot as plt
import statsmodels.api as sm
from scipy.linalg import inv
from numpy import cumsum
import openpyxl
import xlrd
#import xlwt
from scipy import stats
from sklearn.decomposition import PCA
import statsmodels.api as sm
from scipy.stats import zscore
import statsmodels.api as sm
import numpy as np
import pandas as pd
from statsmodels.regression.linear_model import OLS
#from statsmodels.api import ols
import statsmodels.formula.api as smf
import pdb
import scipy.stats
from statsmodels.api import OLS
from sklearn.preprocessing import StandardScaler
import random



from sklearn.linear_model import LinearRegression


import sys
import warnings
if not sys.warnoptions:
    warnings.simplefilter("ignore")

    
N = norm.cdf
ln = np.log
e = np.exp
sqrt = np.sqrt

In [20]:
GW = np.load('Program_generate_GW1_predictors.npy')


In [21]:
dataset = pd.read_excel("Returns_short_interest_data.xlsx")
datasheet = "GW variables"
%run Functions.ipynb



In [22]:
############# Line 1-133

input_file = pd.read_excel("Returns_short_interest_data.xlsx")
input_sheet = "GW variables"

Rfree_lag=pd.read_excel("Returns_short_interest_data.xlsx", sheet_name=0, usecols="K")
Rfree_lag = Rfree_lag[1223:1727]
Rfree_lag = Rfree_lag.values

R_SP500=pd.read_excel("Returns_short_interest_data.xlsx", sheet_name=0, usecols="Q")
R_SP500 = R_SP500[1224:1728]
R_SP500 = R_SP500.values

r = np.log(1 + R_SP500) - np.log(1 + Rfree_lag)
print("Equity risk premium, ann % summary stats (mean, vol, Sharpe ratio)")

mean_r = np.mean(r)
std_r = np.std(r)
result = [12 * mean_r, np.sqrt(12) * std_r, np.sqrt(12) * mean_r / std_r]
print(result)


stats_GW = np.column_stack((np.mean(GW, axis=0), np.median(GW, axis=0), np.percentile(GW, 1, axis=0),
                            np.percentile(GW, 99, axis=0), np.std(GW, axis=0)))

print("Predictor variables, summary stats")
print("Mean, median, 1st percentile, 99th percentile, std dev")

rho_GW = np.full((GW.shape[1], GW.shape[1]), np.nan)
for i in range(GW.shape[1]):
    rho_GW[i, 0] = np.corrcoef(GW[1:, i], GW[:-1, i])[0, 1]

GW_adjust = GW.copy()
GW_adjust[:, 6:9] = -GW[:, 6:9]
GW_adjust[:, 13:15] = -GW[:, 13:15]
GW_standardize = stats.zscore(GW_adjust, axis=0, ddof=1)


X = GW_standardize.copy()
X = np.delete(X, [3, 10], axis=1)
X = zscore(X, axis=0)

pca = PCA(n_components=3)
score = pca.fit_transform(X)
PC_GW = zscore(score, axis=0, ddof=1)

df = pd.read_excel('Returns_short_interest_data.xlsx', sheet_name='Short interest')
EWSI = pd.read_excel("Returns_short_interest_data.xlsx", sheet_name=1, usecols="B")
EWSI = EWSI[0:1727]
EWSI = EWSI.values
log_EWSI = np.log(EWSI)

####################################################################################
#Compute log(EWSI) deviation from linear trend
X_linear = np.column_stack((np.ones((len(log_EWSI), 1)), np.arange(1, len(log_EWSI) + 1).reshape(-1, 1)))


model = sm.OLS(log_EWSI, X_linear)
results_linear = model.fit()
SII = zscore(results_linear.resid, ddof=1)
SII = SII.reshape(-1, 1)
#SII = pd.read_excel("IMPORT_SII.xlsx")
#SII=pd.read_excel("IMPORT_SII.xlsx", sheet_name=0, usecols="A")
#SII = SII[0:504]
#SII = SII.values
#SII.shape

short_interest = np.column_stack((EWSI, SII))
stats_short_interest = np.array([np.mean(short_interest, axis=0),
np.median(short_interest, axis=0),
np.percentile(short_interest, 1, axis=0),
np.percentile(short_interest, 99, axis=0),
np.std(short_interest, axis=0)])
stats_short_interest= np.transpose(stats_short_interest)
print('EWSI & SII, summary stats')
print('Mean, median, 1st percentile, 99th percentile, std dev')
print(stats_short_interest)
print('EWSI decadal means')
decadal_mu = [    EWSI[:12*10].mean(),
    EWSI[12*10:12*20].mean(),
    EWSI[12*20:12*30].mean(),
    EWSI[12*30:].mean()
]
decadal_mu= np.array(decadal_mu)
decadal_mu= decadal_mu.reshape(1,4)
print("Decadal means:", decadal_mu)
rho_SII = [np.corrcoef(column[1:], column[:-1])[0, 1] if len(np.unique(column)) > 1 and not np.isnan(column).any() and np.std(column) != 0 else np.nan for column in SII.T]
print("Correlation between SII[t] and SII[t-1]:", rho_SII)





data = np.concatenate((GW, SII), axis=1)
predictor_correlation = np.corrcoef(data, rowvar=False)


Equity risk premium, ann % summary stats (mean, vol, Sharpe ratio)
[0.04881754629095901, 0.15527207292755063, 0.3144000422647612]
Predictor variables, summary stats
Mean, median, 1st percentile, 99th percentile, std dev
EWSI & SII, summary stats
Mean, median, 1st percentile, 99th percentile, std dev
[[ 2.14642219  1.3059583   0.2222474   7.81501063  1.98253028]
 [-0.         -0.08911899 -2.1083649   2.4384891   0.99900744]]
EWSI decadal means
Decadal means: [[0.31037796 0.90580082 1.81983608 4.98246529]]
Correlation between SII[t] and SII[t-1]: [0.9590948991871402]


In [23]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'Summary statistics'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='w') as writer:
    pd.DataFrame(stats_GW).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=1, header=False, index=False)
    pd.DataFrame(rho_GW).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=12, header=False, index=False)
    pd.DataFrame(stats_short_interest).to_excel(writer, sheet_name=output_sheet, startrow=20, startcol=1, header=False, index=False)
    pd.DataFrame(decadal_mu).to_excel(writer, sheet_name=output_sheet, startrow=20, startcol=7, header=False, index=False)
    pd.DataFrame(rho_SII).to_excel(writer, sheet_name=output_sheet, startrow=21, startcol=12, header=False, index=False)

output_sheet = 'Predictor correlations'
with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
     pd.DataFrame(predictor_correlation).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=1, header=False, index=False)

output_sheet = 'Figures'
with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(SII).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=1, header=False, index=False)
    pd.DataFrame(log_EWSI).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=4, header=False, index=False)

In [6]:
#Compute cumulative returns 

h = np.array([1, 3, 6, 12])
#h = h.reshape(1, -1)
r_h = np.empty((len(r), len(h)))
r_h[:] = np.nan

for j in range(len(h)):
    for t in range(len(r) - (h[j] - 1)):
        r_h[t, j] = np.mean(r[t:t+h[j]])

In [7]:
# Compute in-sample results
beta_hat = np.empty((GW.shape[1]+1, 4, len(h)))
beta_hat[:] = np.nan
beta_hat_PC_SII = np.empty((1, 4, len(h)))
beta_hat_PC_SII[:] = np.nan
IVX_Wald = np.empty((2, len(h)))
IVX_Wald[:] = np.nan
qLL_hat = np.empty((len(h), 1))
qLL_hat[:] = np.nan
#n=1
#j=0
#i=0


for j in range(len(h)):
    for i in range(GW.shape[1]+1):
        if i < GW.shape[1]:
            
            if h[j] == 1:
                X_i_j = np.column_stack((np.ones((len(r_h)-1, 1)), GW_standardize[:-1, i]))
                y = 100 * r_h[1:, 0].reshape(-1, 1)
            else:
                y = 100 * r_h[1:-h[j]+1, j].reshape(-1, 1)
                X_i_j = np.column_stack((np.ones((len(r_h)-1 - h[j]+1, 1)), GW_standardize[:-1-h[j]+1, i]))
                


                


            nlag = h[j]
            results_i_j = sm.OLS(y, X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})

            beta_hat[i, :, j] = [results_i_j.params[1], results_i_j.tvalues[1], np.nan, 100*results_i_j.rsquared]

        
        if i == GW.shape[1]:
            if h[j] == 1:
                X_i_j = np.column_stack((np.ones((len(r_h) - 1, 1)), -SII[:-1]))
                y = 100 * r_h[1:, 0].reshape(-1, 1)
            else:
                y = 100 * r_h[1:-h[j]+1, j].reshape(-1, 1)
                X_i_j = np.column_stack((np.ones((len(r_h) - 1 - h[j]+1, 1)), -SII[:-1 - h[j]+1]))

            results_i_j = sm.OLS(y, X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            beta_hat[i, :, j] = [results_i_j.params[1], results_i_j.tvalues[1], np.nan, 100 * results_i_j.rsquared]

            _, IVX_Wald_i_j, pval_i_j = Compute_IVX_Wald(r, -SII, h[j], 0, 0.99)
            IVX_Wald[:, j] = [IVX_Wald_i_j, pval_i_j]

            if h[j] == 1:
                #y_i_j = r_h[1:, 0].reshape(-1,1)
                y_i_j = r_h[1:, j].reshape(-1, 1)
                X_i_j = -SII[:-1]
                Z_i_j = np.ones((len(r_h) - 1, 1))
            else:
                #y_i_j = r_h[1:-h[j]+1, 0].reshape(-1,1)
                y_i_j = r_h[1:-h[j]+1, j].reshape(-1, 1)
                X_i_j = -SII[:-h[j]]
                Z_i_j = np.ones((len(r_h) - h[j], 1))



            qLL_hat_i_j = Compute_qLL_hat(y_i_j, X_i_j, Z_i_j, h[j])
            qLL_hat[j] = qLL_hat_i_j
            
    if h[j] == 1:
        X_PC_j = np.column_stack((np.ones((len(r_h) - 1, 1)), PC_GW[:-1, :]))
        X_PC_SII_j = np.column_stack((np.ones((len(r_h) - 1, 1)), PC_GW[:-1, :], -SII[:-1]))
        y_PC_j = 100 * r_h[1:, j].reshape(-1, 1)
    else:
        X_PC_j = np.column_stack((np.ones((len(r_h) - 1 - h[j] + 1, 1)), PC_GW[:-1 - h[j] + 1, :]))
        X_PC_SII_j = np.column_stack((np.ones((len(r_h) - 1 - h[j] + 1, 1)), PC_GW[:-1 - h[j] + 1, :], -SII[:-1 - h[j] + 1]))
        y_PC_j = 100 * r_h[1:-h[j] + 1, j].reshape(-1, 1)
        
    results_PC_j = sm.OLS(y_PC_j, X_PC_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
    results_PC_SII_j = sm.OLS(y_PC_j, X_PC_SII_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
    SSE_reduced_j = np.sum(results_PC_j.resid ** 2)
    SSE_full_j = np.sum(results_PC_SII_j.resid ** 2)
    partial_rsqr_j = (SSE_reduced_j - SSE_full_j) / SSE_reduced_j
    beta_hat_PC_SII[0, :, j] = [results_PC_SII_j.params[-1], results_PC_SII_j.tvalues[-1], np.nan, 100 * partial_rsqr_j]
           

In [8]:
# Compute fixed-regressor wild bootstrap p-values

X_sink = np.column_stack((GW_standardize, -SII[:, 0]))
X_sink = np.delete(X_sink, [3, 10], axis=1)
X_sink = np.column_stack((np.ones(len(r_h)), X_sink))
epsilon_hat = np.empty((len(r_h) - 1, r.shape[1]), dtype=np.float64)
epsilon_hat[:] = np.nan
for k in range(r.shape[1]):
    results_k = sm.OLS(r_h[1:, k], X_sink[:-1, :]).fit()
    epsilon_hat[:, k] = results_k.resid

In [9]:
B = 1000
beta_hat_tstat_star = np.empty((B, GW.shape[1] + 1, len(h)))
beta_hat_tstat_star[:] = np.nan
beta_hat_PC_SII_tstat_star = np.empty((B, len(h)))
beta_hat_PC_SII_tstat_star[:] = np.nan

In [10]:
random.seed(0) # for reproducibility

for b in range(B):  
    u_star_b = np.random.randn(len(r) - 1)
    r_star_b = np.empty((len(r), r.shape[1]), dtype=np.float64)
    r_star_b[:] = np.nan
    
    
    for k in range(r.shape[1]):
        r_star_b[:, k] = np.concatenate(([r[0, k]], r[:, k].mean() + epsilon_hat[:, k] * u_star_b))
    
    r_h_star_b = np.empty((len(r_h), len(h), r.shape[1]), dtype=np.float64)
    r_h_star_b[:] = np.nan

    for j in range(len(h)):
        for k in range(r.shape[1]):
            for t in range(len(r) - (h[j] - 1)):
                r_h_star_b[t, j] = r_star_b[t:t + h[j],k].mean()

        
    for j in range(len(h)):
        for i in range(GW.shape[1]+1):
            if i < GW.shape[1]:           
                X_i_j = np.column_stack((np.ones(len(r_h) - h[j]),GW_standardize[: - h[j] , i]))
                if j == 0:
                    results_i_j_star_b = sm.OLS(100 * r_h_star_b[1:, j].reshape(-1,1), X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                else: 
                    results_i_j_star_b = sm.OLS(100 * r_h_star_b[1:len(r_h_star_b) - (h[j] - 1), j].reshape(-1,1), X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                    

            else:
                X_i_j = np.column_stack((np.ones(len(r_h)  - h[j]), -SII[: - h[j]]))
                if j == 0: 
                    results_i_j_star_b = sm.OLS(100 * r_h_star_b[1:, j].reshape(-1, 1), X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                else: 
                    results_i_j_star_b = sm.OLS(100 * r_h_star_b[1:len(r_h_star_b) - (h[j] - 1), j].reshape(-1, 1), X_i_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            beta_hat_tstat_star[b, i, j] = results_i_j_star_b.tvalues[1]
        

        X_PC_SII_j = np.column_stack((np.ones(len(r_h) - 1 - (h[j] - 1)),PC_GW[:-1 - (h[j] - 1), :], -SII[:-1 - (h[j] - 1), :]))
        if j ==0: 
            results_PC_SII_j_star_b = sm.OLS(100 * r_h_star_b[1:, j].reshape(-1, 1),X_PC_SII_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        else: 
            results_PC_SII_j_star_b = sm.OLS(100 * r_h_star_b[1:len(r_h_star_b) - (h[j] - 1), j], X_PC_SII_j).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_PC_SII_tstat_star[b, j] = results_PC_SII_j_star_b.tvalues[1]



In [11]:
for j in range(len(h)):
    for i in range(GW.shape[1]+1):
        beta_hat[i, 2, j] = np.sum(beta_hat_tstat_star[:, i, j] > beta_hat[i, 1, j]) / B
    beta_hat_PC_SII[0, 2, j] = np.sum(beta_hat_PC_SII_tstat_star[:, j] > beta_hat_PC_SII[0, 1, j]) / B

In [12]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'In-sample PR results'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(beta_hat[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=1, header=False, index=False)
    pd.DataFrame(beta_hat_PC_SII[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=21, startcol=1, header=False, index=False)
    pd.DataFrame(beta_hat[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=6, header=False, index=False)
    pd.DataFrame(beta_hat_PC_SII[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=21, startcol=6, header=False, index=False)
    pd.DataFrame(beta_hat[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=11, header=False, index=False)
    pd.DataFrame(beta_hat_PC_SII[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=21, startcol=11, header=False, index=False)
    pd.DataFrame(beta_hat[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=16, header=False, index=False)
    pd.DataFrame(beta_hat_PC_SII[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=21, startcol=16, header=False, index=False)

In [13]:
############################## Compute out-of-sample forecasts   
    

T = len(r)
in_sample_end=1989
R = (in_sample_end - 1972) * 12
P = T - R  # out-of-sample period
FC_PM = np.empty((P, 1))
FC_PM[:] = np.nan
FC_PR = np.empty((P, GW.shape[1] + 1, len(h)))
FC_PR[:] = np.nan
FC_alt_detrend = np.empty((P, 3, len(h)))
FC_alt_detrend[:] = np.nan
MA_size = 60



for p in range(P):
    #print(p)
    #FC_PM[p-1] = np.mean(r[:R+0])
    result = np.mean(r[:R + (p)])
    FC_PM[p] = result
    
    
    
    for j in range(len(h)):
    # Goyal-Welch predictors
        for i in range(GW.shape[1]):
            X_i_j_p = np.concatenate((np.ones((R+(p-1)-h[j]+1, 1)), GW[:R+(p)-h[j], i].reshape(-1, 1)), axis=1) 
            results_i_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_i_j_p).fit()
            FC_PR[p, i, j] = np.array([1, GW[R+p-1, i]]).dot(results_i_j_p.params)
        
        X_linear_p = np.concatenate((np.ones((R+p, 1)), np.arange(1, R+p+1).reshape(-1,1)), axis=1)
        results_linear_p = sm.OLS(log_EWSI[0:R+p], X_linear_p).fit()
        SII_p = zscore(results_linear_p.resid).reshape(-1, 1)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j], :]), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j], X_SII_j_p).fit()
        FC_PR[p, GW.shape[1], j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        X_quadratic_p = np.concatenate((X_linear_p, np.arange(1, R+p+1).reshape(-1, 1)**2), axis=1)
        results_quadratic_p = sm.OLS(log_EWSI[:R+p], X_quadratic_p).fit()
        SII_p = stats.zscore(results_quadratic_p.resid).reshape(-1, 1)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j], :]), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_SII_j_p).fit()
        FC_alt_detrend[p, 0, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        X_cubic_p = np.concatenate((X_quadratic_p, np.arange(1, R+p+1).reshape(-1, 1)**3), axis=1)
        results_cubic_p = sm.OLS(log_EWSI[:R+p], X_cubic_p).fit()
        SII_p = stats.zscore(results_cubic_p.resid)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j]].reshape(-1, 1)), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_SII_j_p).fit()
        FC_alt_detrend[p, 1, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        SII_p = np.empty((R + (p ), 1))
        SII_p[:] = np.nan
        
        for t in range(MA_size-1, R + p+1):
            SII_p[t - 1] = log_EWSI[t - 1] - np.mean(log_EWSI[t - MA_size:t])
        SII_p[MA_size-1:] = zscore(SII_p[MA_size-1:], axis=0,ddof=1)
        X_SII_j_p = np.hstack((np.ones((R + (p ) - h[j] - (MA_size - 1), 1)), SII_p[MA_size - 1:R + (p ) - h[j]]))
        results_SII_j_p = sm.OLS(r_h[MA_size:R + p+1 - h[j], j], X_SII_j_p).fit()
        FC_alt_detrend[p, 2, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)

In [14]:
##############Evaluate forecasts
R2OS_PR = np.empty((GW.shape[1] + 1, 2, len(h)))
R2OS_PR[:] = np.nan

R2OS_alt_detrend = np.empty((FC_alt_detrend.shape[1], 2, len(h)))
R2OS_alt_detrend[:] = np.nan

lambda_ = np.empty((GW.shape[1], 4, len(h)))
lambda_[:] = np.nan
j=0

for j in range(len(h)):
    if j == 0:
        actual_j = r_h[R:, j].reshape(-1,1)
        u_PM_j = actual_j - FC_PM
        u_PR_j = np.kron(np.ones((1, FC_PR.shape[1])), actual_j) - FC_PR[:, :, j]
        u_alt_detrend_j = np.kron(np.ones((1, FC_alt_detrend.shape[1])), actual_j) - FC_alt_detrend[:, :, j]

    else:
        actual_j = r_h[R:, j][:-(h[j] - 1)].reshape(-1,1)
        u_PM_j = actual_j - FC_PM[:-h[j] + 1]
        u_PR_j = np.kron(np.ones((1, FC_PR.shape[1])), actual_j) - FC_PR[:(-h[j] + 1), :, j]
        u_alt_detrend_j = np.kron(np.ones((1, FC_alt_detrend.shape[1])), actual_j) - FC_alt_detrend[:(-h[j] + 1), :, j]



    MSFE_PM_j = np.mean(np.square(u_PM_j))
    MSFE_PR_j = np.mean(np.square(u_PR_j), axis=0).reshape(-1,1).T
    MSFE_alt_detrend_j = np.mean(np.square(u_alt_detrend_j), axis=0).reshape(-1,1).T
    R2OS_PR_j = 100 * (1 - MSFE_PR_j / MSFE_PM_j)
    R2OS_alt_detrend_j = 100 * (1 - MSFE_alt_detrend_j / MSFE_PM_j)
    R2OS_PR[:, 0, j] = R2OS_PR_j
    R2OS_alt_detrend[:, 0, j] = R2OS_alt_detrend_j.ravel()
    L_j=h[j]
  
    for i in range(GW.shape[1] + 1):
        if j == 0:
            f_CW_i_j = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_PR_j[:, i].reshape(-1, 1)) + np.square(FC_PM.reshape(-1, 1) - FC_PR[:, i, j].reshape(-1, 1))
        else:
            f_CW_i_j = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_PR_j[:, i].reshape(-1, 1)) + np.square(FC_PM[:-h[j] + 1].reshape(-1, 1) - FC_PR[:-h[j] + 1, i, j].reshape(-1, 1))

        results_CW_i_j = sm.regression.linear_model.OLS(f_CW_i_j, np.ones((f_CW_i_j.shape[0], 1))).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        R2OS_PR[i, 1, j] = results_CW_i_j.tvalues[0]
        
        if i <= GW.shape[1] - 1:
            results_HLN_i_j = OLS(u_PR_j[:, i], u_PR_j[:, i] - u_PR_j[:, -1]).fit()
            d_i_j = ((u_PR_j[:, i] - u_PR_j[:, -1]) * u_PR_j[:, i]).reshape(-1,1)
            d_i_j_bar = np.mean(d_i_j)
            Q_i_j = (1 / len(u_PR_j[:, i])) * np.sum(np.square(d_i_j))
            
            for l in range(1, L_j + 1):
                Q_i_j += (1 / len(u_PR_j[:, i])) * (1 - (l / (L_j + 1))) * np.sum(d_i_j[l:] * d_i_j[:-l])

            HLN_i_j = np.sqrt(len(u_PR_j[:, i])) * (Q_i_j ** (-0.5)) * d_i_j_bar
            lambda_[i, :2, j] = [results_HLN_i_j.params[0], HLN_i_j]
            results_HLN_i_j = OLS(u_PR_j[:, -1], u_PR_j[:, -1] - u_PR_j[:, i]).fit()
            d_i_j = ((u_PR_j[:, -1] - u_PR_j[:, i]) * u_PR_j[:, -1]).reshape(-1,1)
            d_i_j_bar = np.mean(d_i_j)
            Q_i_j = (1 / len(u_PR_j[:, -1])) * np.sum(np.square(d_i_j))
            for l in range(1, L_j + 1):
                Q_i_j += (1 / len(u_PR_j[:, -1])) * (1 - (l / (L_j + 1))) * np.sum(d_i_j[l:] * d_i_j[:-l])

            HLN_i_j = np.sqrt(len(u_PR_j[:, -1])) * (Q_i_j ** (-0.5)) * d_i_j_bar
            lambda_[i, 2:4, j] = [results_HLN_i_j.params[0], HLN_i_j]
            
            for k in range(FC_alt_detrend.shape[1]):

                if j == 0:
                    f_CW_j_k = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_alt_detrend_j[:, k].reshape(-1, 1)) + \
                        np.square(FC_PM.reshape(-1, 1) - FC_alt_detrend[:, k, j].reshape(-1, 1))
                else:
                    f_CW_j_k = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_alt_detrend_j[:, k].reshape(-1, 1)) + \
                        np.square(FC_PM[:-h[j] + 1].reshape(-1, 1) - FC_alt_detrend[:-h[j] + 1, k, j].reshape(-1, 1))

                    


                results_CW_j_k = sm.regression.linear_model.OLS(f_CW_j_k, np.ones((f_CW_j_k.shape[0], 1))).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                

                R2OS_alt_detrend[k, 1, j] = results_CW_j_k.tvalues[0]  # <-- Corrected indentation

               


In [15]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'R2OS statistics'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(R2OS_PR[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=1, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=1, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=4, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=4, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=7, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=7, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=10, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=10, header=False, index=False)

output_sheet='Forecast encompassing'
with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(lambda_[:,:2,0]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=1, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,0]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=13, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,1]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=4, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,1]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=16, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,2]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=7, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,2]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=19, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,3]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=10, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,3]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=22, header=False, index=False)

In [16]:
############################## Compute out-of-sample forecasts  1990-2007 
    

T = len(r)-96
in_sample_end=1989
R = (in_sample_end - 1972) * 12
P = T - R  # out-of-sample period
FC_PM = np.empty((P, 1))
FC_PM[:] = np.nan
FC_PR = np.empty((P, GW.shape[1] + 1, len(h)))
FC_PR[:] = np.nan
FC_alt_detrend = np.empty((P, 3, len(h)))
FC_alt_detrend[:] = np.nan
MA_size = 60



for p in range(P):
    #print(p)
    #FC_PM[p-1] = np.mean(r[:R+0])
    result = np.mean(r[:R + (p)])
    FC_PM[p] = result
    
    
    
    for j in range(len(h)):
    # Goyal-Welch predictors
        for i in range(GW.shape[1]):
            X_i_j_p = np.concatenate((np.ones((R+(p-1)-h[j]+1, 1)), GW[:R+(p)-h[j], i].reshape(-1, 1)), axis=1) 
            results_i_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_i_j_p).fit()
            FC_PR[p, i, j] = np.array([1, GW[R+p-1, i]]).dot(results_i_j_p.params)
        
        X_linear_p = np.concatenate((np.ones((R+p, 1)), np.arange(1, R+p+1).reshape(-1,1)), axis=1)
        results_linear_p = sm.OLS(log_EWSI[0:R+p], X_linear_p).fit()
        SII_p = zscore(results_linear_p.resid).reshape(-1, 1)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j], :]), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j], X_SII_j_p).fit()
        FC_PR[p, GW.shape[1], j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        X_quadratic_p = np.concatenate((X_linear_p, np.arange(1, R+p+1).reshape(-1, 1)**2), axis=1)
        results_quadratic_p = sm.OLS(log_EWSI[:R+p], X_quadratic_p).fit()
        SII_p = stats.zscore(results_quadratic_p.resid).reshape(-1, 1)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j], :]), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_SII_j_p).fit()
        FC_alt_detrend[p, 0, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        X_cubic_p = np.concatenate((X_quadratic_p, np.arange(1, R+p+1).reshape(-1, 1)**3), axis=1)
        results_cubic_p = sm.OLS(log_EWSI[:R+p], X_cubic_p).fit()
        SII_p = stats.zscore(results_cubic_p.resid)
        X_SII_j_p = np.concatenate((np.ones((R+p-h[j], 1)), SII_p[:R+p-h[j]].reshape(-1, 1)), axis=1)
        results_SII_j_p = sm.OLS(r_h[1:R+p-h[j]+1, j].reshape(-1, 1), X_SII_j_p).fit()
        FC_alt_detrend[p, 1, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)
        
        SII_p = np.empty((R + (p ), 1))
        SII_p[:] = np.nan
        
        for t in range(MA_size-1, R + p+1):
            SII_p[t - 1] = log_EWSI[t - 1] - np.mean(log_EWSI[t - MA_size:t])
        SII_p[MA_size-1:] = zscore(SII_p[MA_size-1:], axis=0,ddof=1)
        X_SII_j_p = np.hstack((np.ones((R + (p ) - h[j] - (MA_size - 1), 1)), SII_p[MA_size - 1:R + (p ) - h[j]]))
        results_SII_j_p = sm.OLS(r_h[MA_size:R + p+1 - h[j], j], X_SII_j_p).fit()
        FC_alt_detrend[p, 2, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)



In [17]:
##############Evaluate forecasts 1990-2007
R2OS_PR = np.empty((GW.shape[1] + 1, 2, len(h)))
R2OS_PR[:] = np.nan

R2OS_alt_detrend = np.empty((FC_alt_detrend.shape[1], 2, len(h)))
R2OS_alt_detrend[:] = np.nan

lambda_ = np.empty((GW.shape[1], 4, len(h)))
lambda_[:] = np.nan
j=0

for j in range(len(h)):
    if j == 0:
        actual_j = r_h[R:-96, j].reshape(-1,1)
        u_PM_j = actual_j - FC_PM
        u_PR_j = np.kron(np.ones((1, FC_PR.shape[1])), actual_j) - FC_PR[:, :, j]
        u_alt_detrend_j = np.kron(np.ones((1, FC_alt_detrend.shape[1])), actual_j) - FC_alt_detrend[:, :, j]

    else:
        actual_j = r_h[R:-96, j][:-(h[j] - 1)].reshape(-1,1)
        u_PM_j = actual_j - FC_PM[:-h[j] + 1]
        u_PR_j = np.kron(np.ones((1, FC_PR.shape[1])), actual_j) - FC_PR[:(-h[j] + 1), :, j]
        u_alt_detrend_j = np.kron(np.ones((1, FC_alt_detrend.shape[1])), actual_j) - FC_alt_detrend[:(-h[j] + 1), :, j]



    MSFE_PM_j = np.mean(np.square(u_PM_j))
    MSFE_PR_j = np.mean(np.square(u_PR_j), axis=0).reshape(-1,1).T
    MSFE_alt_detrend_j = np.mean(np.square(u_alt_detrend_j), axis=0).reshape(-1,1).T
    R2OS_PR_j = 100 * (1 - MSFE_PR_j / MSFE_PM_j)
    R2OS_alt_detrend_j = 100 * (1 - MSFE_alt_detrend_j / MSFE_PM_j)
    R2OS_PR[:, 0, j] = R2OS_PR_j
    R2OS_alt_detrend[:, 0, j] = R2OS_alt_detrend_j.ravel()
    L_j=h[j]
  
    for i in range(GW.shape[1] + 1):
        if j == 0:
            f_CW_i_j = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_PR_j[:, i].reshape(-1, 1)) + np.square(FC_PM.reshape(-1, 1) - FC_PR[:, i, j].reshape(-1, 1))
        else:
            f_CW_i_j = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_PR_j[:, i].reshape(-1, 1)) + np.square(FC_PM[:-h[j] + 1].reshape(-1, 1) - FC_PR[:-h[j] + 1, i, j].reshape(-1, 1))

        results_CW_i_j = sm.regression.linear_model.OLS(f_CW_i_j, np.ones((f_CW_i_j.shape[0], 1))).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        R2OS_PR[i, 1, j] = results_CW_i_j.tvalues[0]
        
        if i <= GW.shape[1] - 1:
            results_HLN_i_j = OLS(u_PR_j[:, i], u_PR_j[:, i] - u_PR_j[:, -1]).fit()
            d_i_j = ((u_PR_j[:, i] - u_PR_j[:, -1]) * u_PR_j[:, i]).reshape(-1,1)
            d_i_j_bar = np.mean(d_i_j)
            Q_i_j = (1 / len(u_PR_j[:, i])) * np.sum(np.square(d_i_j))
            
            for l in range(1, L_j + 1):
                Q_i_j += (1 / len(u_PR_j[:, i])) * (1 - (l / (L_j + 1))) * np.sum(d_i_j[l:] * d_i_j[:-l])

            HLN_i_j = np.sqrt(len(u_PR_j[:, i])) * (Q_i_j ** (-0.5)) * d_i_j_bar
            lambda_[i, :2, j] = [results_HLN_i_j.params[0], HLN_i_j]
            results_HLN_i_j = OLS(u_PR_j[:, i], u_PR_j[:, -1] - u_PR_j[:, i]).fit()
            d_i_j = ((u_PR_j[:, -1] - u_PR_j[:, i]) * u_PR_j[:, -1]).reshape(-1,1)
            d_i_j_bar = np.mean(d_i_j)
            Q_i_j = (1 / len(u_PR_j[:, -1])) * np.sum(np.square(d_i_j))
            for l in range(1, L_j + 1):
                Q_i_j += (1 / len(u_PR_j[:, -1])) * (1 - (l / (L_j + 1))) * np.sum(d_i_j[l:] * d_i_j[:-l])

            HLN_i_j = np.sqrt(len(u_PR_j[:, -1])) * (Q_i_j ** (-0.5)) * d_i_j_bar
            lambda_[i, 2:4, j] = [results_HLN_i_j.params[0], HLN_i_j]
            
            for k in range(FC_alt_detrend.shape[1]):

                if j == 0:
                    f_CW_j_k = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_alt_detrend_j[:, k].reshape(-1, 1)) + \
                        np.square(FC_PM.reshape(-1, 1) - FC_alt_detrend[:, k, j].reshape(-1, 1))
                else:
                    f_CW_j_k = np.square(u_PM_j.reshape(-1, 1)) - np.square(u_alt_detrend_j[:, k].reshape(-1, 1)) + \
                        np.square(FC_PM[:-h[j] + 1].reshape(-1, 1) - FC_alt_detrend[:-h[j] + 1, k, j].reshape(-1, 1))

                    


                results_CW_j_k = sm.regression.linear_model.OLS(f_CW_j_k, np.ones((f_CW_j_k.shape[0], 1))).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                

                R2OS_alt_detrend[k, 1, j] = results_CW_j_k.tvalues[0]  # <-- Corrected indentation



In [18]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'R2OS statistics'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(R2OS_PR[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=15, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=15, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=18, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=18, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=21, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=21, header=False, index=False)
    pd.DataFrame(R2OS_PR[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=2, startcol=24, header=False, index=False)
    pd.DataFrame(R2OS_alt_detrend[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=24, header=False, index=False)
output_sheet='Forecast encompassing'
with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(lambda_[:,:2,0]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=1, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,0]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=13, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,1]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=4, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,1]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=16, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,2]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=7, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,2]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=19, header=False, index=False)
    pd.DataFrame(lambda_[:,:2,3]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=10, header=False, index=False)
    pd.DataFrame(lambda_[:,2:4,3]).to_excel(writer, sheet_name=output_sheet, startrow=25, startcol=22, header=False, index=False)